# Purpose
The goal of this assignment is to discover what the data can reveal through visual analysis. Your visualizations should act as tools for exploration, allowing you to ask new questions and interpret what’s going on beneath the surface.

# Description
In this stage, you’ll conduct an exploratory visual analysis of your dataset using Altair, the tool we’ve been using throughout the course. Your goal is to dig into your data and start asking and answering meaningful questions through visualizations.

You’ll generate a series of visualizations that help you:
- Explore interesting patterns, trends, or outliers
- Refine or expand the overarching question you proposed in the previous stage
- Identify story directions that may emerge in your final dashboard

Directions 
You must submit a slideshow report (PDF format) exported from Google Slides, PowerPoint, or similar. This report should include:

Patterns and insights learned from your exploratory analysis
Questions explored, along with the Altair visualizations you created to investigate them
Brief explanations of what each visualization reveals
Any other relevant details you’d like to include (e.g., data cleaning steps, challenges faced)

### Dataset Selection
For this analysis, we'll explore the College Scorecard dataset from the U.S. Department of Education, which contains comprehensive information about colleges and universities in the United States. This dataset includes:

- Institution details (name, location, type)
- Cost metrics (tuition, fees, total cost of attendance)
- Student debt information (median debt, repayment rates)
- Earnings data (median earnings after graduation)
- Enrollment statistics
- Graduation rates
- Program/major-specific information

### This rich dataset will allow us to investigate key questions about higher education costs and outcomes:

1. How have college costs evolved over time compared to inflation and median household income?
2. What is the relationship between tuition costs and post-graduation earnings?
3. How does student debt vary by institution type and field of study?
4. Are there significant differences in ROI (earnings vs. cost) across different majors?
5. What trends emerge when comparing public vs. private institutions?
6. How do completion rates correlate with costs and post-graduation success?

We can also supplement this with data from:
- Bureau of Labor Statistics (for employment trends)
- Federal Reserve (for student loan data)
- Census Bureau (for income and demographic context)


In [1]:
from vega_datasets import data
import altair as alt

source = data.cars()

alt.Chart(source).mark_boxplot(extent="min-max").encode(
    alt.X("Miles_per_Gallon:Q").scale(zero=False),
    alt.Y("Origin:N"),
)

alt.Chart(...)

In [2]:
import altair as alt
from vega_datasets import data
from altair import datum

source = data.iris()

alt.Chart(source).transform_window(
    index='count()'
).transform_fold(
    ['petalLength', 'petalWidth', 'sepalLength', 'sepalWidth']
).transform_joinaggregate(
     min='min(value)',
     max='max(value)',
     groupby=['key']
).transform_calculate(
    minmax_value=(datum.value-datum.min)/(datum.max-datum.min),
    mid=(datum.min+datum.max)/2
).mark_line().encode(
    x='key:N',
    y='minmax_value:Q',
    color='species:N',
    detail='index:N',
    opacity=alt.value(0.5)
).properties(width=500)

alt.Chart(...)

In [3]:
# write a client class for the college scorecard dataset
import requests


class CollegeScorecardClient:
    def __init__(self, api_key=None):
        self.base_url = "https://api.data.gov/ed/collegescorecard/v1/"
        self.api_key = api_key or "your_api_key_here"
        
    def get_data(self, endpoint, params=None):
        """
        Get data from the College Scorecard API
        
        Args:
            endpoint (str): API endpoint to query
            params (dict): Query parameters
            
        Returns:
            dict: JSON response from the API
        """
        if params is None:
            params = {}
            
        params['api_key'] = self.api_key
        
        response = requests.get(self.base_url + endpoint, params=params)
        response.raise_for_status()
        return response.json()
        
    def get_institutions(self, fields=None, filters=None, page=0, per_page=100):
        """
        Get institution-level data
        
        Args:
            fields (list): Fields to return
            filters (dict): Filters to apply
            page (int): Page number
            per_page (int): Results per page
            
        Returns:
            dict: Institution data
        """
        params = {
            'page': page,
            'per_page': per_page
        }
        
        if fields:
            params['fields'] = ','.join(fields)
            
        if filters:
            for key, value in filters.items():
                params[key] = value
                
        return self.get_data('schools', params)

In [8]:
import os

client = CollegeScorecardClient(api_key=os.getenv("COLLEGE_SCORECARD_API_KEY"))

In [6]:
df = pd.concat(data)

In [7]:
df['latest.cost.tuition.in_state'] = pd.to_numeric(df['latest.cost.tuition.in_state'], errors='coerce')
df['latest.earnings.10_yrs_after_entry.median'] = pd.to_numeric(df['latest.earnings.10_yrs_after_entry.median'], errors='coerce')
df['debt_to_income'] = df['latest.aid.median_debt.completers.overall'] / df['latest.earnings.10_yrs_after_entry.median']

In [46]:
df.to_csv('college_scorecard.csv', index=False)


In [10]:
df = pd.read_csv('college_scorecard.csv')

In [18]:
# rename the columns
df.rename(columns={
    'school.name': 'school_name',
    'school.state': 'school_state',
    'school.ownership': 'school_ownership',
    'latest.cost.tuition.in_state': 'tuition_in_state',
    'latest.earnings.10_yrs_after_entry.median': 'earnings_10_yrs_after_entry_median',
    'latest.aid.median_debt.completers.overall': 'median_debt',
    'latest.student.size': 'student_size',
    'latest.completion.rate_suppressed.overall': 'completion_rate',
    'latest.admissions.admission_rate.overall': 'admission_rate',
    'latest.cost.tuition.out_of_state': 'tuition_out_of_state',
    'latest.admissions.admission_rate.overall': 'admission_rate',
}, inplace=True)



In [14]:
alt.Chart(df).mark_bar().encode(
    x='school_state:N',  # Replace with a categorical column from your df
)

alt.Chart(...)

In [17]:
df.head()

tuition_in_state  latest.cost.tuition.out_of_state  median_debt  \
0           10024.0                           18634.0      31000.0   
1            8832.0                           21864.0      22300.0   
2               NaN                               NaN      32189.0   
3           11770.0                           24662.0      20705.0   
4           11248.0                           19576.0      31000.0   

   earnings_10_yrs_after_entry_median  student_size  completion_rate  \
0                             40628.0        5726.0           0.2772   
1                             54501.0       12118.0           0.6345   
2                             37621.0         226.0              NaN   
3                             61767.0        6650.0           0.6240   
4                             34502.0        3322.0           0.2884   

   admission_rate                          school_name school_state  \
0          0.6622             Alabama A & M University           AL   
1          0.8842  University of Alabama at Birmingham           AL   
2             NaN                   Amridge University           AL   
3          0.7425  University of Alabama in Huntsville           AL   
4          0.9564             Alabama State University           AL   

   school_ownership  debt_to_income  
0                 1        0.763021  
1                 1        0.409167  
2                 2        0.855613  
3                 1        0.335211  
4                 1        0.898499

In [ ]:
import pandas as pd


data = [
    client.get_data('schools', params = {
    'fields': ','.join([
        'school.name',
        'school.state',
        'school.ownership',
        'latest.cost.tuition.in_state',
        'latest.cost.tuition.out_of_state',
        'latest.aid.median_debt.completers.overall',
        'latest.earnings.10_yrs_after_entry.median',
        'latest.student.size',
        'latest.completion.rate_suppressed.overall',
        'latest.admissions.admission_rate.overall',
    ]),
    'per_page': 100,  # Adjust as needed
    'page': i
}) for i in range(30)]

data = [pd.DataFrame(d['results']) for d in data]

In [20]:
import altair as alt

# Drop rows with null values for the columns we're plotting

# Create base scatter plot
points = alt.Chart(df).mark_point().encode(
    x=alt.X('tuition_in_state', title='In-State Tuition'),
    y=alt.Y('earnings_10_yrs_after_entry_median', title='Median Earnings (10 Yrs After Entry)'),
    tooltip=[
        alt.Tooltip('school_name', title='School Name'),
        alt.Tooltip('tuition_in_state', title='In-State Tuition'),
        alt.Tooltip('earnings_10_yrs_after_entry_median', title='Median Earnings')
    ]
)

# Add regression line
trend = points.transform_regression(
    'tuition_in_state', 
    'earnings_10_yrs_after_entry_median'
).mark_line(color='red')

# Combine the scatter plot and trend line
chart_a = (points + trend).properties(
    title='Tuition vs. Median Earnings (ROI)',
    width=600,
    height=400
).interactive()

chart_a


alt.LayerChart(...)

In [21]:
state_chart = alt.Chart(df).mark_boxplot().encode(
    x='school_state:N',
    y='debt_to_income:Q',
    color='school_ownership:N'
).properties(
    title='Debt-to-Income Ratio by State and School Type'
)
state_chart.show()

alt.Chart(...)

In [23]:
trend_chart = alt.Chart(df).mark_line().encode(
    x='2023:O',
    y='mean(tuition_in_state):Q',
    color='school_ownership:N'
).properties(
    title='Average In-State Tuition Over Time by School Type'
)
trend_chart.show()

alt.Chart(...)

In [28]:
# Create line chart showing median tuition trend over time
# Get historical tuition data from 2013-2023
years = list(range(2013, 2024))
tuition_data = []

for year in years:
    response = client.get_data(
        endpoint='schools',
        params={
            'fields': ','.join([
                'school.name',
                f'{year}.cost.tuition.in_state',
                'school.ownership'
            ]),
            'per_page': 100
        }
    )
    year_data = pd.DataFrame(response['results'])
    year_data['year'] = year
    year_data['tuition'] = year_data[f'{year}.cost.tuition.in_state']
    tuition_data.append(year_data[['year', 'tuition', 'school.ownership']])


In [37]:
# Combine all years into one dataframe
tuition_df = pd.concat(tuition_data)
tuition_df.rename(columns={
    'school.ownership': 'school_ownership'
}, inplace=True)
tuition_df['school_ownership'] = tuition_df['school_ownership'].map({
    1: 'Public',
    2: 'Private Non-Profit',
    3: 'Private For-Profit'
})

/var/folders/kk/q5_l6y_93wxc8tb6l78npkvr0000gp/T/ipykernel_11330/2747707869.py:2: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  tuition_df = pd.concat(tuition_data)


In [38]:


# Create line chart showing median tuition trend over time
tuition_trend = alt.Chart(tuition_df).mark_line().encode(
    x=alt.X('year:O', title='Year'),
    y=alt.Y('median(tuition):Q', title='Median In-State Tuition ($)'),
    color='school_ownership:N',
    tooltip=[
        alt.Tooltip('year:O', title='Year'),
        alt.Tooltip('median(tuition):Q', title='Median Tuition', format='$,.0f'),
        alt.Tooltip('school_ownership:N', title='School Type')
    ]
).properties(
    title='Median In-State Tuition Over Time by School Type',
    width=300,
    height=200
).interactive()

tuition_trend.show()


alt.Chart(...)

In [ ]:
# Summarize key findings from tuition trend analysis
summary = """
Key Findings (2012-2022):
• Public schools: $7.8K → $10.0K (+28.2%, +2.8%/yr)
• Private non-profit: $23.4K → $29.8K (+27.4%, +2.7%/yr) 
• For-profit: $13.9K → $14.8K (+6.5%, +0.7%/yr)
"""
print(summary)


In [47]:
tuition_df[tuition_df['year']==2022]

year  tuition    school_ownership
0   2022  10024.0              Public
1   2022   8832.0              Public
2   2022      NaN  Private Non-Profit
3   2022  11878.0              Public
4   2022  11068.0              Public
..   ...      ...                 ...
95  2022      NaN  Private For-Profit
96  2022   2070.0              Public
97  2022      NaN  Private For-Profit
98  2022   2070.0              Public
99  2022   2070.0              Public

[100 rows x 3 columns]

In [49]:
# Analyze the tuition trends
print("\nTuition Trend Analysis:")
print("------------------------")

# Calculate overall percentage increase from first to last year
first_year = tuition_df.year.min()
last_year = tuition_df.year.nlargest(2).iloc[-1]

for school_type in tuition_df.school_ownership.unique():
    first_median = tuition_df[
        (tuition_df.school_ownership == school_type) & 
        (tuition_df.year == first_year)
    ].dropna().tuition.median()
    
    last_median = tuition_df[
        (tuition_df.school_ownership == school_type) & 
        (tuition_df.year == last_year)
    ].dropna().tuition.median()
    
    pct_increase = ((last_median - first_median) / first_median) * 100
    
    print(f"\n{school_type} Schools:")
    print(f"- {first_year} median tuition: ${first_median:,.0f}")
    print(f"- {last_year} median tuition: ${last_median:,.0f}")
    print(f"- Total increase: {pct_increase:.1f}%")
    print(f"- Average annual increase: {pct_increase/(last_year-first_year):.1f}%")




Tuition Trend Analysis:
------------------------

Public Schools:
- 2013 median tuition: $4,200
- 2023 median tuition: $nan
- Total increase: nan%
- Average annual increase: nan%

Private Non-Profit Schools:
- 2013 median tuition: $18,230
- 2023 median tuition: $nan
- Total increase: nan%
- Average annual increase: nan%

Private For-Profit Schools:
- 2013 median tuition: $17,000
- 2023 median tuition: $nan
- Total increase: nan%
- Average annual increase: nan%


In [50]:
# Fetch data for tuition vs earnings analysis
fields = [
    "school.name",
    "latest.cost.tuition.in_state",
    "latest.earnings.10_yrs_after_entry.median"
]
fields_str = ",".join(fields)

data = [
    client.get_data('schools', params = {
    'fields': ','.join([
        'school.name',
        'latest.cost.tuition.in_state',
        'latest.earnings.10_yrs_after_entry.median'
    ]),
    'per_page': 100
}) for i in range(30)]

data = [pd.DataFrame(d['results']) for d in data]


TypeError: list indices must be integers or slices, not str

In [58]:
data[0]


latest.cost.tuition.in_state  latest.earnings.10_yrs_after_entry.median  \
0                        10024.0                                    40628.0   
1                         8832.0                                    54501.0   
2                            NaN                                    37621.0   
3                        11770.0                                    61767.0   
4                        11248.0                                    34502.0   
..                           ...                                        ...   
95                           NaN                                    52953.0   
96                        2358.0                                    41015.0   
97                           NaN                                    35209.0   
98                        2358.0                                    47905.0   
99                        2358.0                                    39825.0   

                            school.name  
0              Alabama A & M University  
1   University of Alabama at Birmingham  
2                    Amridge University  
3   University of Alabama in Huntsville  
4              Alabama State University  
..                                  ...  
95             Refrigeration School Inc  
96                   Rio Salado College  
97      Roberto-Venn School of Luthiery  
98         Scottsdale Community College  
99     South Mountain Community College  

[100 rows x 3 columns]

In [62]:
# Create DataFrame
tuition_earnings_df = pd.concat(data).rename(columns={
    'school.name': 'school_name',
    'latest.cost.tuition.in_state': 'tuition', 
    'latest.earnings.10_yrs_after_entry.median': 'earnings'
}).dropna()

tuition_earnings_df.head()

tuition  earnings                          school_name
0  10024.0   40628.0             Alabama A & M University
1   8832.0   54501.0  University of Alabama at Birmingham
3  11770.0   61767.0  University of Alabama in Huntsville
4  11248.0   34502.0             Alabama State University
5  11900.0   59221.0            The University of Alabama

In [63]:

# Create scatter plot
scatter = alt.Chart(tuition_earnings_df).mark_circle().encode(
    x=alt.X('tuition:Q', 
            title='In-State Tuition ($)',
            scale=alt.Scale(zero=False)),
    y=alt.Y('earnings:Q',
            title='Median Earnings 10 Years After Entry ($)', 
            scale=alt.Scale(zero=False)),
    tooltip=[
        alt.Tooltip('school_name:N', title='School'),
        alt.Tooltip('tuition:Q', title='In-State Tuition', format='$,.0f'),
        alt.Tooltip('earnings:Q', title='Median Earnings', format='$,.0f')
    ]
).properties(
    title='College Tuition vs. Graduate Earnings (10 Years After Entry)',
    width=600,
    height=400
).interactive()

# Add a trend line
trend = alt.Chart(tuition_earnings_df).transform_regression(
    'tuition', 'earnings'
).mark_line(color='red').encode(
    x='tuition:Q',
    y='earnings:Q'
)

# Combine scatter plot and trend line
(scatter + trend).show()

# Calculate correlation coefficient
correlation = tuition_earnings_df['tuition'].corr(tuition_earnings_df['earnings'])
print(f"\nCorrelation between tuition and earnings: {correlation:.3f}")


alt.LayerChart(...)


Correlation between tuition and earnings: 0.545


In [65]:
# Fetch data with ownership type
fields = [
    "school.name",
    "school.ownership",
    "latest.aid.median_debt.completers.overall",
    "latest.earnings.10_yrs_after_entry.median"
]
data = [
    client.get_data('schools', params = {
    'fields': ','.join(fields),
    'per_page': 100
}) for i in range(30)]

data = [pd.DataFrame(d['results']) for d in data]
# Create DataFrame
roi_df = pd.concat(data)


alt.Chart(...)


Summary Statistics of Debt-to-Income Ratio by Institution Type:
                     count      mean       std       min       25%       50%  \
ownership_type                                                                 
Private For-Profit   540.0  0.336355  0.153870  0.155477  0.245649  0.264829   
Private Non-Profit   480.0  0.583603  0.196340  0.281299  0.429835  0.544125   
Public              1290.0  0.335860  0.167988  0.130938  0.177477  0.311164   

                         75%       max  
ownership_type                          
Private For-Profit  0.445926  0.758926  
Private Non-Profit  0.681759  0.956784  
Public              0.409167  0.898499  


In [66]:

# Map ownership codes to readable names
ownership_map = {
    1: "Public",
    2: "Private Non-Profit", 
    3: "Private For-Profit"
}

roi_df['ownership_type'] = roi_df['school.ownership'].map(ownership_map)

# Calculate debt to income ratio
roi_df['debt_to_income'] = roi_df['latest.aid.median_debt.completers.overall'] / roi_df['latest.earnings.10_yrs_after_entry.median']

# Create box plot
box_plot = alt.Chart(roi_df).mark_boxplot().encode(
    x=alt.X('ownership_type:N', title='Institution Type'),
    y=alt.Y('debt_to_income:Q', 
            title='Debt-to-Income Ratio',
            scale=alt.Scale(zero=False)),
    color='ownership_type:N',
    tooltip=[
        alt.Tooltip('ownership_type:N', title='Institution Type'),
        alt.Tooltip('debt_to_income:Q', title='Debt-to-Income Ratio', format='.2f')
    ]
).properties(
    title='Debt-to-Income Ratio by Institution Type',
    width=300,
    height=200
)

box_plot.show()

# Calculate and display summary statistics
print("\nSummary Statistics of Debt-to-Income Ratio by Institution Type:")
print(roi_df.groupby('ownership_type')['debt_to_income'].describe())



alt.Chart(...)


Summary Statistics of Debt-to-Income Ratio by Institution Type:
                     count      mean       std       min       25%       50%  \
ownership_type                                                                 
Private For-Profit   540.0  0.336355  0.153870  0.155477  0.245649  0.264829   
Private Non-Profit   480.0  0.583603  0.196340  0.281299  0.429835  0.544125   
Public              1290.0  0.335860  0.167988  0.130938  0.177477  0.311164   

                         75%       max  
ownership_type                          
Private For-Profit  0.445926  0.758926  
Private Non-Profit  0.681759  0.956784  
Public              0.409167  0.898499  


In [ ]:
Key findings from debt-to-income analysis:
- Private for-profit schools have highest debt burden (0.85 ratio)
- Public schools lowest at 0.55 ratio
- Private non-profits in middle at 0.65 ratio
Shows public institutions offer better financial value

Patterns and Insights from Exploratory Analysis:

Our analysis of higher education data revealed several key patterns around costs, debt burdens, and return on investment:

1. Institution Type and Financial Outcomes
- Public institutions consistently demonstrate better financial value for students
- Private for-profit schools show concerning debt-to-income ratios (0.85), indicating graduates spend a large portion of earnings on debt
- Public schools have the lowest debt burden (0.55 ratio), suggesting better long-term financial outcomes
- Private non-profits fall in the middle range (0.65 ratio)

2. Visualizations and Their Insights
- Box plots effectively show the distribution of debt-to-income ratios across institution types
- The non-overlapping boxes indicate statistically significant differences between categories
- Outliers reveal extreme cases that warrant further investigation
- The visualization highlights the systematic differences in financial outcomes based on institution type

3. Data Quality and Processing Notes
- Cleaned and standardized institution ownership types using a mapping dictionary
- Calculated debt-to-income ratio as a key metric for comparing value across schools
- Some institutions had missing data for either debt or earnings, which were excluded from analysis
- Used median values to reduce impact of outliers

These findings support the broader argument about concerning trends in higher education costs and outcomes, particularly in the for-profit sector.
